# CHAPTER 10 - SQL

## 1. CREATING TABLES

### Basic

A database is made up of tables. Tables are made up of columns and rows. A database can be considered like an Excel file and the sheets in your Excel file are like tables. The power of database comes from joining different tables based on shared column information/name between tables and filtering and aggregating rows. SQL is the language that allows you to create, update, delete, filter, and aggregate tables. Often the first step in data wrangling is to extract the data you need from an SQL table. Sometimes you might even have to parse data and populate into a database before you can start using it.

### Sqlite3

- SQLite3 supports three primitive data types: INTEGER, REAL, TEXT, and BLOB.
- SQLite3 is dynamically typed. This means that even if you specify a column to be data type real or integer, you can insert a string type into it. If the string type can be cast into a numeric type, it will be, otherwise it will be left as is. 
- If you apply a sum or other math function to a column with mixed data types, only the numerical values will be used.

### Creating a Table

Tables are created using the `CREATE TABLE <name_of_table>` directive followed by a pair of parenthesis inside
which is a definition of each of the columns, meaning column names, their respective data type, and if they 
allow `NULL` values or not, default is to allow `NULL` values, and if they are a `PRIMARY KEY`. In addition, create statements can link a table column to another
column using the `REFERENCES` keyword.

#### A simple table
The following SQL command creates a students table with six columns 

```SQL
CREATE TABLE Students (
    last_name TEXT, 
    first_name TEXT, 
    username TEXT, 
    exam1 REAL, 
    exam2 REAL, 
    exam3 REAL
);
```

#### Inserting some values into a table
You can insert values into a table using the `INSERT INTO <name_of_table> (<name_of_column_1>, <name_of_column_2>, ....)
VALUES (<value_of_column_1>, <value_of_column_1>, ...);` The following SQL statements insert some values into a table with some
variations.

#### Valid Insert statements

```SQL
INSERT INTO Students (last_name, first_name, username, exam1, exam2, exam3) VALUES ('Doe', 'John', 'johndoe', 98, 76, 89);
INSERT INTO Students (first_name, last_name, username, exam1, exam2, exam3) VALUES ('Emily', 'Shepard', 'eshepard', 88, 96, 90);
INSERT INTO Students VALUES ('Doe', 'Jane', 'janedoe', 89, 64, 39);
INSERT INTO Students (last_name, first_name, username) VALUES ('Smith', 'John', 'johnsmith');
INSERT INTO Students (exam1, exam2, exam3) VALUES (78, 99, 83);
INSERT INTO Students (exam1, exam2, exam3) VALUES ('25', '33', '45');
INSERT INTO Students  VALUES (56, 32, 33, 'Eaglestone', 'Ken', 'keagle');
```

1. In the first insert statement all columns names and their corresponding values are supplied in the order of create table statement. 
2. In the second insert statement, the order of the columns names are changed (first and last name), but SQLite3 will put them in the correct column. 
3. In the third insert statement, if all the number of values supplied correspond to the number of rows, then SQLite3 will insert them into the table in the order of the create statement. 
4. In the fourth insert statement, it is possible to only supply some values since by default all columns allow null values. 
5. In the fifth insert statement, only the names exams values a provided. This is allowed because by default all columns allow null values, but his is poor database design. 
6. In the sixth insert statement, only exams values are provided, but they are type string. SQLite3 will convert them to `REAL` before inserting them into the table. 
7. In the seventh insert statement, all the values are inserted into the wrong column, which is allowed by SQLite3 since it is dynamically types, so be very careful!

#### Invalid Insert Statement

```SQL
INSERT INTO Students  VALUES ('Smith', 'John', 'johnsmith');
```

```SQL
Execution finished with errors.
Result: table Students has 6 columns but 3 values were supplied
At line 1:
INSERT INTO Students  VALUES ('Smith', 'Jake', 'johnsmith');
```

### Adding `NOT NULL` constraint

In the previous table we highlighted a poor database design where you could insert exams scores without a student. 
We fix this by making the student fields `NOT NULL`, meaning they have to be specified. 

Note you can drop a table using `DROP TABLE <name_of_table>`. 

```SQL
DROP TABLE Students;
CREATE TABLE Students (
    last_name TEXT NOT NULL, 
    first_name TEXT NOT NULL, 
    username TEXT NOT NULL, 
    exam1 REAL, 
    exam2 REAL, 
    exam3 REAL
);
```

- Note that the two separate SQL statements are separated by `;`. 

If we know attempt to enter a student exam score without the name fields, SQLite3 will raise an error. 

```SQL
INSERT INTO Students('exam1') VALUES ('52');
```

```SQL
Execution finished with errors.
Result: NOT NULL constraint failed: Students.last_name
At line 10:
INSERT INTO Students('exam1') VALUES ('52');
```

### Primary Keys

When you create any table, SQLite3 adds a hidden column called `rowid`. 

```SQL
DROP TABLE IF EXISTS Teachers;
CREATE TABLE Teachers(
  TeacherName  TEXT NOT NULL
);

INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
SELECT rowid, * FROM Teachers;
```

In [1]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/primary_key_example.db')

sql_statements = """
DROP TABLE IF EXISTS Teachers;
CREATE TABLE Teachers(
  TeacherName  TEXT NOT NULL
);

INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
SELECT rowid, * FROM Teachers;
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)


sql_statement = """
SELECT * FROM Teachers;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

sql_statement = """
SELECT rowid, * FROM Teachers;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

TeacherName
0  John Smith
1  John Smith

rowid TeacherName
0      1  John Smith
1      2  John Smith

Note: `DROP TABLE IF EXISTS Teachers;` is used to drop the table if it exists. This is useful if you want to run the create statement over and over again with changes. 

When you create a table that has an INTEGER NOT NULL PRIMARY KEY column, this column is the alias of the rowid column.

It uniquely identifies a row in a table. Primary keys have the following properties:
1. Primary keys can consist of one or more columns, meaning multiple columns combined can uniquely define a row. 
2. Primary keys cannot be duplicated since they uniquely identify a row in a table. 
3. Primary keys cannot be NULL since a blank value cannot identify a row in a table. 
4. There can only be one primary key per table. Note that this is different from a primary key being made up of multiple tables. 
5. Primary keys are indexed automatically. 
6. INTEGER primary keys are auto-increment fields starting at 1.

```SQL
DROP TABLE Teachers;
CREATE TABLE Teachers (
   TeacherId INTEGER NOT NULL PRIMARY KEY,
   TeacherName  TEXT NOT NULL
);
INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
SELECT * FROM Teachers;
```

In [2]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('primary_key_example.db')

sql_statements = """
DROP TABLE IF EXISTS Teachers;
CREATE TABLE Teachers (
   TeacherId INTEGER NOT NULL PRIMARY KEY,
   TeacherName  TEXT NOT NULL
);
INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
INSERT INTO Teachers ('TeacherName') VALUES ('John Smith');
SELECT * FROM Teachers;
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)


sql_statement = """
SELECT * FROM Teachers;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Adding a `unique` constraint

In the previous examples teachers table, it is possible to add multiple John Smiths. How can you identify one John Smith
from another John Smith. One way would be to assign teachers unique IDs that cannot be reused. A column can be made unique
by using the `UNIQUE` keyword. 

```SQL
DROP TABLE Teachers;
CREATE TABLE Teachers (
   TeacherId INTEGER NOT NULL PRIMARY KEY,
   TeacherName  TEXT NOT NULL,
   TeacherEmployeeID INTEGER NOT NULL,
   UNIQUE (TeacherEmployeeID)
);
INSERT INTO Teachers ('TeacherName', 'TeacherEmployeeID') VALUES ('John Smith', 100001);
INSERT INTO Teachers ('TeacherName', 'TeacherEmployeeID') VALUES ('John Smith', 100002);
SELECT * FROM Teachers;
```

In [3]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('primary_key_example.db')

sql_statements = """
DROP TABLE Teachers;
CREATE TABLE Teachers (
   TeacherId INTEGER NOT NULL PRIMARY KEY,
   TeacherName  TEXT NOT NULL,
   TeacherEmployeeID INTEGER NOT NULL,
   UNIQUE (TeacherEmployeeID)
);
INSERT INTO Teachers ('TeacherName', 'TeacherEmployeeID') VALUES ('John Smith', 100001);
INSERT INTO Teachers ('TeacherName', 'TeacherEmployeeID') VALUES ('John Smith', 100002);
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

sql_statement = """
SELECT * FROM Teachers;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Foreign Keys

What is a foreign key? In a relational database, you can relate one table to another table. 
The two tables can be related if and only if both tables have one column in common. 
This column has to be declared as a INTEGER/TEXT data type that cannot be NULL and has the PRIMARY KEY constraint, e.g., 
`<name_of_column> INTEGER NOT NULL PRIMARY KEY`.It seems INTEGER foreign keys are preferred over TEXT ones. See the following
references:
   - https://stackoverflow.com/questions/3162202/sql-primary-key-integer-vs-varchar
   - https://stackoverflow.com/questions/9206391/int-vs-varchar-datatype-for-primary-keys
<br>

- Foreign key constraint are NOT enabled by default in SQLite. Execute `PRAGMA foreign_keys = ON;` to enable foreign key constraint. 

### Creating a relationship

```SQL
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS  Courses;
DROP TABLE IF EXISTS Teachers;
CREATE TABLE Teachers (
   TeacherId INTEGER NOT NULL PRIMARY KEY,
   TeacherName  TEXT NOT NULL,
   TeacherEmployeeID INTEGER NOT NULL,
   UNIQUE (TeacherEmployeeID)
);

CREATE TABLE Courses(
  CourseId     INTEGER NOT NULL PRIMARY KEY, 
  CourseName   TEXT NOT NULL,
  CourseShortID   TEXT NOT NULL,
  TeacherId INTEGER NOT NULL,
  FOREIGN KEY(TeacherId) REFERENCES Teachers(TeacherId),
  UNIQUE (CourseName, CourseShortID)
);

INSERT INTO Teachers (TeacherName, TeacherEmployeeID)
VALUES ('Melissa Larson', 10001);

INSERT INTO Teachers (TeacherName,TeacherEmployeeID)
VALUES ('Christopher Smith', 10002);

INSERT INTO Courses (CourseName, CourseShortID, TeacherId)
VALUES ('Introduction to Python', 'EAS503', 1);

INSERT INTO Courses (CourseName, CourseShortID, TeacherId)
VALUES ('Introduction to Probability', 'EAS506', 2);
```

In [4]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('teachers_courses.db')

sql_statements = """
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS  Courses;
DROP TABLE IF EXISTS Teachers;
CREATE TABLE Teachers (
   TeacherId INTEGER NOT NULL PRIMARY KEY,
   TeacherName  TEXT NOT NULL,
   TeacherEmployeeID INTEGER NOT NULL,
   UNIQUE (TeacherEmployeeID)
);

CREATE TABLE Courses(
  CourseId     INTEGER NOT NULL PRIMARY KEY, 
  CourseName   TEXT NOT NULL,
  CourseShortID   TEXT NOT NULL,
  TeacherId INTEGER NOT NULL,
  FOREIGN KEY(TeacherId) REFERENCES Teachers(TeacherId),
  UNIQUE (CourseName, CourseShortID)
);

INSERT INTO Teachers (TeacherName, TeacherEmployeeID)
VALUES ('Melissa Larson', 10001);

INSERT INTO Teachers (TeacherName,TeacherEmployeeID)
VALUES ('Christopher Smith', 10002);

INSERT INTO Courses (CourseName, CourseShortID, TeacherId)
VALUES ('Introduction to Python', 'EAS503', 1);

INSERT INTO Courses (CourseName, CourseShortID, TeacherId)
VALUES ('Introduction to Probability', 'EAS506', 2);
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

### Using the relationship

#### Method 1 -- explicitly link two tables
- Note this method will result in duplicated TeacherID fields if you select all the columns using '*'.


```SQL
SELECT 
    *
FROM 
    Teachers t
INNER JOIN 
    Courses c ON t.TeacherId = c.TeacherId;
```

In [5]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('teachers_courses.db')

sql_statement = """
SELECT 
    *
FROM 
    Teachers t
INNER JOIN 
    Courses c ON t.TeacherId = c.TeacherId;
"""

df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

TeacherId        TeacherName  TeacherEmployeeID  CourseId   
0          1     Melissa Larson              10001         1  \
1          2  Christopher Smith              10002         2   

                    CourseName CourseShortID  
0       Introduction to Python        EAS503  
1  Introduction to Probability        EAS506

```SQL
SELECT 
    t.TeacherName, 
    c.CourseName, 
    c.CourseShortID
FROM 
    Teachers t
INNER JOIN 
    Courses c ON t.TeacherId = c.TeacherId;
```

In [6]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('teachers_courses.db')

sql_statement = """
SELECT 
    t.TeacherName, 
    c.CourseName, 
    c.CourseShortID
FROM 
    Teachers t
INNER JOIN 
    Courses c ON t.TeacherId = c.TeacherId;
"""

df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

TeacherName                   CourseName CourseShortID
0     Melissa Larson       Introduction to Python        EAS503
1  Christopher Smith  Introduction to Probability        EAS506

#### Method 2 -- let SQLite infers join condition -- but you specify the shared column name
- Note this method will NOT result in duplicated TeacherID fields if you select all the columns using '*'.
```SQL
SELECT 
    *
FROM 
    Teachers t
INNER JOIN Courses c USING(TeacherId);
```

In [7]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('teachers_courses.db')

sql_statement = """
SELECT  
    *
FROM 
    Teachers t
INNER JOIN Courses c USING(TeacherId);
"""

df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

TeacherId        TeacherName  TeacherEmployeeID  CourseId   
0          1     Melissa Larson              10001         1  \
1          2  Christopher Smith              10002         2   

                    CourseName CourseShortID  
0       Introduction to Python        EAS503  
1  Introduction to Probability        EAS506

```SQL
SELECT 
    t.TeacherName, 
    c.CourseName, 
    c.CourseShortID
FROM 
    Teachers t
INNER JOIN Courses c USING(TeacherId);
```

In [8]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('teachers_courses.db')

sql_statement = """
SELECT 
    t.TeacherName, 
    c.CourseName, 
    c.CourseShortID
FROM 
    Teachers t
INNER JOIN Courses c USING(TeacherId);
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

TeacherName                   CourseName CourseShortID
0     Melissa Larson       Introduction to Python        EAS503
1  Christopher Smith  Introduction to Probability        EAS506

### Joining Tables

There are two types of joins
- Inner Join
- Outer Join
    - Left Outer Join (or Left Join)
    - Right Outer Join (or Right Join)
    - Full Outer Join (or Full Join)
Example database: `join_example_database.db`
    - Ref: https://www.diffen.com/difference/Inner_Join_vs_Outer_Join

In [9]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/join_example_database.db')

sql_statement = """
SELECT
    *
FROM Prices 
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

sql_statement = """
SELECT
    *
FROM Quantities 
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')
display(df)

PK   PRODUCT  PRICE
0   1  Potatoes      3
1   2  Avacados      4
2   3     Kiwis      2
3   4    Onions      1
4   5    Melons      5
5   6   Oranges      5
6   7  Tomatoes      6

PK   PRODUCT  QUANTITY
0   1  Potatoes        45
1   2  Avacados        63
2   3     Kiwis        19
3   4    Onions        20
4   5    Melons        66
5   6  Broccoli        27
6   7    Squash        92

#### Inner Join
```SQL
SELECT 
    Prices.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM Prices 
INNER JOIN Quantities ON Prices.Product = Quantities.Product;
```

In [10]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/join_example_database.db')

sql_statement = """
SELECT 
    Prices.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM Prices 
INNER JOIN Quantities ON Prices.Product = Quantities.Product;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Left Join

```SQL
SELECT 
    Prices.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM 
    Prices
LEFT OUTER JOIN Quantities ON Prices.Product = Quantities.Product;
```

In [11]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/join_example_database.db')

sql_statement = """
SELECT 
    Prices.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM 
    Prices
LEFT OUTER JOIN Quantities ON Prices.Product = Quantities.Product;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Right Join -- Doesn't work in SQLITE3

```SQL
SELECT 
    Prices.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM 
    Prices 
RIGHT OUTER JOIN Quantities ON Prices.Product = Quantities.Product;
```

```SQL
Execution finished with errors.
Result: RIGHT and FULL OUTER JOINs are not currently supported
At line 1:
SELECT 
    Prices.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM 
    Prices 
RIGHT OUTER JOIN Quantities
```

#### Right Join by doing Left Join 
Change the order of the tables to emulate right join!

```SQL
SELECT 
    Quantities.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM 
    Quantities 
LEFT OUTER JOIN Prices ON Quantities.Product = Prices.Product;
```

In [12]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/join_example_database.db')

sql_statement = """
SELECT 
    Quantities.Product, 
    Prices.Price, 
    Quantities.Quantity
FROM 
    Quantities 
LEFT OUTER JOIN Prices ON Quantities.Product = Prices.Product;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Full Outer join -- does not work in SQLite3

```SQL
SELECT Prices.Product, Prices.Price, Quantities.Quantity
FROM Prices FULL OUTER JOIN Quantities
ON Prices.Product = Quantities.Product;
```

```SQL
Execution finished with errors.
Result: RIGHT and FULL OUTER JOINs are not currently supported
At line 1:
SELECT Prices.Product, Prices.Price, Quantities.Quantity
FROM Prices FULL OUTER JOIN Quantities
```

### Joining Multiple Tables

```SQL
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS Cars;
DROP TABLE IF EXISTS MakeModels;
DROP TABLE IF EXISTS Colors;


CREATE TABLE Colors (
   color_id INTEGER NOT NULL PRIMARY KEY,
   color  TEXT NOT NULL,
   UNIQUE (color)
);

CREATE TABLE MakeModels (
  make_model_id     INTEGER NOT NULL PRIMARY KEY, 
  Make   TEXT NOT NULL,
  Model   TEXT NOT NULL,
  Year INTEGER NOT NULL,
  UNIQUE (Make, Model, Year)
);

CREATE TABLE Cars (
   car_id INTEGER NOT NULL PRIMARY KEY,
   make_model_id INTEGER NOT NULL,
   color_id INTEGER NOT NULL,
   available INTEGER NOT NULL,
   FOREIGN KEY(make_model_id) REFERENCES MakeModels(make_model_id),
   FOREIGN KEY(color_id) REFERENCES Colors(color_id)
);

INSERT INTO Colors (color) VALUES ('Red');
INSERT INTO Colors (color) VALUES ('Blue');
INSERT INTO Colors (color) VALUES ('Green');

INSERT INTO MakeModels (Make, Model, Year) VALUES ('Ford', 'Explorer', 2019);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Toyota', 'Camry', 2010);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Honda', 'Accord', 2015);

INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (2, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 3, 0);
```

In [13]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statements = """
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS Cars;
DROP TABLE IF EXISTS MakeModels;
DROP TABLE IF EXISTS Colors;

CREATE TABLE Colors (
   color_id INTEGER NOT NULL PRIMARY KEY,
   color  TEXT NOT NULL,
   UNIQUE (color)
);

CREATE TABLE MakeModels (
  make_model_id     INTEGER NOT NULL PRIMARY KEY, 
  Make   TEXT NOT NULL,
  Model   TEXT NOT NULL,
  Year INTEGER NOT NULL,
  UNIQUE (Make, Model, Year)
);

CREATE TABLE Cars (
   car_id INTEGER NOT NULL PRIMARY KEY,
   make_model_id INTEGER NOT NULL,
   color_id INTEGER NOT NULL,
   available INTEGER NOT NULL,
   FOREIGN KEY(make_model_id) REFERENCES MakeModels(make_model_id),
   FOREIGN KEY(color_id) REFERENCES Colors(color_id)
);

INSERT INTO Colors (color) VALUES ('Red');
INSERT INTO Colors (color) VALUES ('Blue');
INSERT INTO Colors (color) VALUES ('Green');

INSERT INTO MakeModels (Make, Model, Year) VALUES ('Ford', 'Explorer', 2019);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Toyota', 'Camry', 2010);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Honda', 'Accord', 2015);

INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (2, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 3, 0);
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

In [14]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT * FROM Colors;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [15]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT * FROM MakeModels;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [16]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT * FROM Cars;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [17]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Updating Tables

The following tables have typos in them!

```SQL
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS Cars;
DROP TABLE IF EXISTS MakeModels;
DROP TABLE IF EXISTS Colors;


CREATE TABLE Colors (
   color_id INTEGER NOT NULL PRIMARY KEY,
   color  TEXT NOT NULL,
   UNIQUE (color)
);

CREATE TABLE MakeModels (
  make_model_id     INTEGER NOT NULL PRIMARY KEY, 
  Make   TEXT NOT NULL,
  Model   TEXT NOT NULL,
  Year INTEGER NOT NULL,
  UNIQUE (Make, Model, Year)
);

CREATE TABLE Cars (
   car_id INTEGER NOT NULL PRIMARY KEY,
   make_model_id INTEGER NOT NULL,
   color_id INTEGER NOT NULL,
   available INTEGER NOT NULL,
   FOREIGN KEY(make_model_id) REFERENCES MakeModels(make_model_id),
   FOREIGN KEY(color_id) REFERENCES Colors(color_id)
);

INSERT INTO Colors (color) VALUES ('Red');
INSERT INTO Colors (color) VALUES ('Blue');
INSERT INTO Colors (color) VALUES ('Greene'); -- TYPO!!!

INSERT INTO MakeModels (Make, Model, Year) VALUES ('Frd', 'Explorer', 2019); -- TYPO!!!
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Toyota', 'Camrey', 2010); -- TYPO!!!
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Honda', 'Accord', 2015);

INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (2, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 3, 0);
```

In [18]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statements = """
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS Cars;
DROP TABLE IF EXISTS MakeModels;
DROP TABLE IF EXISTS Colors;

CREATE TABLE Colors (
   color_id INTEGER NOT NULL PRIMARY KEY,
   color  TEXT NOT NULL,
   UNIQUE (color)
);

CREATE TABLE MakeModels (
  make_model_id     INTEGER NOT NULL PRIMARY KEY, 
  Make   TEXT NOT NULL,
  Model   TEXT NOT NULL,
  Year INTEGER NOT NULL,
  UNIQUE (Make, Model, Year)
);

CREATE TABLE Cars (
   car_id INTEGER NOT NULL PRIMARY KEY,
   make_model_id INTEGER NOT NULL,
   color_id INTEGER NOT NULL,
   available INTEGER NOT NULL,
   FOREIGN KEY(make_model_id) REFERENCES MakeModels(make_model_id),
   FOREIGN KEY(color_id) REFERENCES Colors(color_id)
);

INSERT INTO Colors (color) VALUES ('Red');
INSERT INTO Colors (color) VALUES ('Blue');
INSERT INTO Colors (color) VALUES ('Greene'); -- TYPO!!!

INSERT INTO MakeModels (Make, Model, Year) VALUES ('Frd', 'Explorer', 2019); -- TYPO!!!
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Toyota', 'Camrey', 2010); -- TYPO!!!
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Honda', 'Accord', 2015);

INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (2, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 3, 0);
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Update Color

```SQL
UPDATE Colors
SET color = 'Green'
WHERE color = "Greene";
```

In [19]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
UPDATE Colors
SET color = 'Green'
WHERE color = "Greene";
"""
with conn:
    cur = conn.cursor()
    cur.execute(sql_statement)

```SQL
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
```

In [20]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Update MakeModel

```SQL
UPDATE MakeModels
SET Make = 'Ford'
WHERE Make = "Frd";

UPDATE MakeModels
SET Model = 'Camry'
WHERE Model = "Camrey";
```

In [21]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statements = """
UPDATE MakeModels
SET Make = 'Ford'
WHERE Make = "Frd";

UPDATE MakeModels
SET Model = 'Camry'
WHERE Model = "Camrey";
"""
with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

```SQL
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
```

In [22]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Update Car

```SQL
UPDATE Cars
SET available = 1
WHERE car_id = 6;
```

In [23]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('cars.db')

sql_statement = """
UPDATE Cars
SET available = 1
WHERE car_id = 6;
"""
with conn:
    cur = conn.cursor()
    cur.execute(sql_statement)

```SQL
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
```

In [24]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Simple Delete

You can easily delete a non-referenced row.

```SQL
DELETE FROM Cars
WHERE available = 0;
```

In [25]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
DELETE FROM Cars
WHERE available = 0;
"""
with conn:
    cur = conn.cursor()
    cur.execute(sql_statement)

In [26]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Deleting a referenced row

A referenced row can be deleted or not depending on how the table was defined. By default, a referenced
row cannot be deleted. This default behavior can be changed. You can either set the foreign key to
`ON DELETE SET NULL` or `ON DELETE SET CASCADE`. In the former case, the references to the row being deleted 
is set to `NULL`. In the latter case, the anything that references the row being deleted is also deleted. 

```SQL
DELETE FROM Colors
WHERE color = "Red";
```

```SQL
Execution finished with errors.
Result: FOREIGN KEY constraint failed
At line 1:
DELETE FROM Colors
WHERE color = "Red";
```

```SQL
DELETE FROM Cars
WHERE car_id IN (SELECT car_id from Cars INNER JOIN Colors clr USING(color_id ) WHERE clr.color='Red');
DELETE FROM Colors
WHERE color = "Red";
```

In [27]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statements = """
DELETE FROM Cars
WHERE car_id IN (SELECT car_id from Cars INNER JOIN Colors clr USING(color_id ) WHERE clr.color='Red');
DELETE FROM Colors
WHERE color = "Red";
"""
with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

```SQL
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
```

In [28]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### `ON DELETE`

```SQL
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS Cars;
DROP TABLE IF EXISTS MakeModels;
DROP TABLE IF EXISTS Colors;


CREATE TABLE Colors (
   color_id INTEGER NOT NULL PRIMARY KEY,
   color  TEXT NOT NULL,
   UNIQUE (color)
   
);

CREATE TABLE MakeModels (
  make_model_id     INTEGER NOT NULL PRIMARY KEY, 
  Make   TEXT NOT NULL,
  Model   TEXT NOT NULL,
  Year INTEGER NOT NULL,
  UNIQUE (Make, Model, Year)
);

CREATE TABLE Cars (
   car_id INTEGER NOT NULL PRIMARY KEY,
   make_model_id INTEGER NOT NULL,
   color_id INTEGER, --> Have to allow for NULL values for ON DELETE SET NULL to work!!!!
   available INTEGER NOT NULL,
   FOREIGN KEY(make_model_id) REFERENCES MakeModels(make_model_id) ON DELETE CASCADE,
   FOREIGN KEY(color_id) REFERENCES Colors(color_id) ON DELETE SET NULL
);

INSERT INTO Colors (color) VALUES ('Red');
INSERT INTO Colors (color) VALUES ('Blue');
INSERT INTO Colors (color) VALUES ('Green');

INSERT INTO MakeModels (Make, Model, Year) VALUES ('Ford', 'Explorer', 2019);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Toyota', 'Camry', 2010);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Honda', 'Accord', 2015);

INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (2, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 3, 0);
```

In [29]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statements = """
PRAGMA foreign_keys = ON;
DROP TABLE IF EXISTS Cars;
DROP TABLE IF EXISTS MakeModels;
DROP TABLE IF EXISTS Colors;


CREATE TABLE Colors (
   color_id INTEGER NOT NULL PRIMARY KEY,
   color  TEXT NOT NULL,
   UNIQUE (color)
   
);

CREATE TABLE MakeModels (
  make_model_id     INTEGER NOT NULL PRIMARY KEY, 
  Make   TEXT NOT NULL,
  Model   TEXT NOT NULL,
  Year INTEGER NOT NULL,
  UNIQUE (Make, Model, Year)
);

CREATE TABLE Cars (
   car_id INTEGER NOT NULL PRIMARY KEY,
   make_model_id INTEGER NOT NULL,
   color_id INTEGER, --> Have to allow for NULL values for ON DELETE SET NULL to work!!!!
   available INTEGER NOT NULL,
   FOREIGN KEY(make_model_id) REFERENCES MakeModels(make_model_id) ON DELETE CASCADE,
   FOREIGN KEY(color_id) REFERENCES Colors(color_id) ON DELETE SET NULL
);

INSERT INTO Colors (color) VALUES ('Red');
INSERT INTO Colors (color) VALUES ('Blue');
INSERT INTO Colors (color) VALUES ('Green');

INSERT INTO MakeModels (Make, Model, Year) VALUES ('Ford', 'Explorer', 2019);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Toyota', 'Camry', 2010);
INSERT INTO MakeModels (Make, Model, Year) VALUES ('Honda', 'Accord', 2015);

INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (2, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 1, 1);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (1, 2, 0);
INSERT INTO Cars (make_model_id, color_id, available) VALUES (3, 3, 0);
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

```SQL
DELETE FROM Colors
WHERE color = "Red";

DELETE FROM MakeModels
WHERE make_model_id = 1;
```

In [30]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statements = """
DELETE FROM Colors
WHERE color = "Red";

DELETE FROM MakeModels
WHERE make_model_id = 1;
"""

with conn:
    cur = conn.cursor()
    cur.executescript(sql_statements)

```SQL
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
```

In [31]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    INNER JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    INNER JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

```SQL
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    LEFT JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    LEFT JOIN Colors ON Colors.color_id = Cars.color_id;
```

In [32]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('cars.db')

sql_statement = """
SELECT Cars.car_id, MakeModels.Make, MakeModels.Model, MakeModels.year, Colors.color, Cars.available
FROM Cars
    LEFT JOIN MakeModels ON MakeModels.make_model_id = Cars.make_model_id
    LEFT JOIN Colors ON Colors.color_id = Cars.color_id;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 2. SQL QUERY PRIMER

### Query Clauses

SQL offers six clauses ({ref}`query-clauses`) to query your data. All SQL queries will use at least two clauses, i.e., `SELECT` and `FROM`. 

| **Clause Name** 	| **Purpose**                                                                           	|
| ----------------- | ----------------------------------------------------------------------------------------- |
| SELECT          	| Determines which columns to include in the query's result set                         	|
| FROM            	| Identifies the tables from which to retrieve data and how the tables should be joined 	|
| WHERE           	| Filters out unwanted data                                                                 |
| GROUP BY        	| Used to group rows together by common column values                                       |
| HAVING          	| Filters out unwanted groups                                                               |
| ORDER BY        	| Sorts the rows of the final result set by one or more columns                             |

### Basic query

The most basic SQL query will have a `SELECT` and `FROM` clause. Select lets you choose the columns
you want. In case you want all the columns, you can use `*`, which indicates to SQL you want all the columns. 
The `FROM` clause lets you specify the table you want to query. The following is the most basic SQL query:
You can select all the columns by using `*` after the `SELECT`. Note all SQL queries are terminated 
by a semicolon (`;`). You can format your SQL with as many spaces and tabs as you like. To indicate to SQL
that your query statement is complete, terminate it with a semicolon. 

Query: Select all columns and all rows from the `PatientCorePopulatedTable` table. 

```sql
SELECT
    *
FROM
    PatientCorePopulatedTable;
```

In [33]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    *
FROM
    PatientCorePopulatedTable;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Limit rows

You can limit the number of rows to 10 by adding `LIMIT 10` after the `FROM` clause. 

**Query:** Select all columns and from the `PatientCorePopulatedTable` table and limit to 10 rows. 

```sql
SELECT
    *
FROM
    PatientCorePopulatedTable
LIMIT 10;
```

In [34]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    *
FROM
    PatientCorePopulatedTable
LIMIT 10;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Select some columns

You can select columns from a table by specifying them after the `SELECT` clause. Multiple
columns are separated by a comma (`,`). 

**Query**: Select the PatientID and PatientDateOfBirth columns and limit to 10 rows.

```sql
SELECT
    PatientID,
    PatientDateOfBirth
FROM
    PatientCorePopulatedTable
LIMIT 10;
```

In [35]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    PatientID,
    PatientDateOfBirth
FROM
    PatientCorePopulatedTable
LIMIT 10;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Using column alias

Notice that all the column names are prefixed by `Patient`. You can give columns a different name, meaning an alias. 
There are two ways to do alias. You can put the alias name right after the actual column name, e.g., `PatientID PTID`
or you can use the `AS` keyword to indicate explicitly that you are aliasing a column name, e.g., `PatientID AS PTID`.
Note that if the alias has a space, then it should be in quotes. 

**Query**: Select the PatientID and PatientDateOfBirth columns, but alias PatientID to PTID and PatientDateOfBirth 
to "Date of Birth" and limit to 10 rows.

```sql
SELECT
    PatientID PTID, 
    PatientDateOfBirth AS "Date of Birth"
FROM
    PatientCorePopulatedTable
LIMIT 10;
```

In [36]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    PatientID PTID, 
    PatientDateOfBirth AS "Date of Birth"
FROM
    PatientCorePopulatedTable
LIMIT 10;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Adding columns not from the table

Besides selecting columns in the table, you can also add the following columns to your query:
1. literals such as numbers or strings
2. Math expressions such as `PatientPopulationPercentageBelowPoverty + 1`, or `PatientPopulationPercentageBelowPoverty * 100`

**Query**: Select the PatientID, Hospital, and PatientPopulationPercentageBelowPoverty columns, alias PatientID to PTID, 
make the `Hospital` column 'Buffalo General', multiply `PatientPopulationPercentageBelowPoverty` by 10 and alias it to
`Poverty Level`, and limit to 10 rows. Note that if the alias name has a space, then the name needs to inside of quotes. 

```sql
SELECT
    PatientID PTID, 
    'Buffalo General' Hospital,
    PatientPopulationPercentageBelowPoverty * 10 "Poverty Level"
FROM
    PatientCorePopulatedTable
LIMIT 10;
```

In [37]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    PatientID PTID, 
    'Buffalo General' Hospital,
    PatientPopulationPercentageBelowPoverty * 10 "Poverty Level"
FROM
    PatientCorePopulatedTable
LIMIT 10;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Removing duplicates

In some cases you might get duplicate rows. You remove these duplicate rows by putting the `DISTINCT` keyword
after the `SELECT` keyword. One use of this is to get distinct values of a given column. 

Query: Select only the `PatientMaritalStatus` column from the `PatientCorePopulatedTable` table.

```sql
SELECT
    PatientMaritalStatus
FROM
    PatientCorePopulatedTable;
```

In [38]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    PatientMaritalStatus
FROM
    PatientCorePopulatedTable;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

**Query:** Select the `PatientMaritalStatus` column from the `PatientCorePopulatedTable` table but
only select distinct values. 

```sql
SELECT DISTINCT
    PatientMaritalStatus
FROM
    PatientCorePopulatedTable;
```

In [39]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT DISTINCT
    PatientMaritalStatus
FROM
    PatientCorePopulatedTable;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Removing duplicates with multiple columns

The `DISTINCT` keyword can also be used to find distinct combination of columns. **It is also used sometimes with joins
to remove duplicate rows.**

**Query:** Select  `PatientRace` and `PatientMaritalStatus` columns from the `PatientCorePopulatedTable` table but
only select distinct values. This query finds the distinct combinations of race and martial status. 

```sql
SELECT DISTINCT
    PatientRace,
    PatientMaritalStatus
FROM
    PatientCorePopulatedTable
ORDER BY PatientRace, PatientMaritalStatus
```

In [40]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT DISTINCT
    PatientRace,
    PatientMaritalStatus
FROM
    PatientCorePopulatedTable
ORDER BY PatientRace, PatientMaritalStatus
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### `FROM` multiple tables

The power of SQL lies in the fact that you can combine tables together based on some shared column between
tables. The `FROM` clause allows you to select from multiple tables. 

You should now that there are four types of tables in SQL:
1. Permanent tables (i.e., created using the `CREATE TABLE` statement)
2. Derived tables (i.e., rows returned by a subquery and held in memory)
3. Temporary tables (i.e., volatile data held in memory)
4. Virtual tables (i.e, created using the `CREATE VIEW` statement)

We have been using permanent tables so far. Temporary and virtual tables will be covered later. The following
is an example a derived table. 

#### Derived table
A derived query is a query held in memory. You surround it a pair of parenthesis and give it a name. 

**Query**: Create a subquery called `dx_codes` which selects the `PrimaryDiagnosisCode` and `PrimaryDiagnosisDescription`
columns from the `AdmissionsDiagnosesCorePopulatedTable` where the `AdmissionID` is equal to `1`. Then use this derived query in another query that concatenates the diagnosis code and diagnosis description, e.g., "(M01.X) Direct infection of joint in infectious and parasitic diseases classified elsewhere". Fields and string literals can be concatenated in SQLite using `||`. 

```sql
SELECT '(' || dx_codes.code || ') ' || dx_codes.description AS CodeWDescription
FROM
   (
     SELECT
       PrimaryDiagnosisCode code,
       PrimaryDiagnosisDescription description 
     FROM
       AdmissionsDiagnosesCorePopulatedTable
      WHERE AdmissionID = 1
   ) dx_codes
```

In [41]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT '(' || dx_codes.code || ') ' || dx_codes.description AS CodeWDescription
FROM
   (
     SELECT
       PrimaryDiagnosisCode code,
       PrimaryDiagnosisDescription description 
     FROM
       AdmissionsDiagnosesCorePopulatedTable
      WHERE AdmissionID = 1
   ) dx_codes
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### The `WHERE` Clause

The `WHERE` clause allows you to filter out unwanted rows. For string fields, you can use the equality operator (`=`) or 
the `LIKE` operator. For numerical and date fields, you can use all the usually operators such as greater than, less than, etc. 
`WHERE` clauses can be combined using `AND` and `OR`. Parenthesis can be used to clarify grouping of the clauses. The
`WHERE` clauses are put after the `FROM` clause. 

**Query:** Select all patients from `PatientCorePopulatedTable` table that are either married and african american or married and white and 
the `PatientPopulationPercentageBelowPoverty` is above 15. Select the following columns: PatientID, PatientRace, PatientMaritalStatus and
PatientPopulationPercentageBelowPoverty. 

```sql
SELECT 
  PatientID, 
  PatientRace, 
  PatientMaritalStatus,
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
WHERE ((PatientRace = 'White' AND PatientMaritalStatus	= 'Married') OR (PatientRace = 'African American' AND PatientMaritalStatus = 'Married'))
  AND PatientPopulationPercentageBelowPoverty > 15
```

In [42]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
  PatientID, 
  PatientRace, 
  PatientMaritalStatus,
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
WHERE (
	(
		PatientRace = 'White' AND PatientMaritalStatus	= 'Married') 
		OR (PatientRace = 'African American' AND PatientMaritalStatus	= 'Married')
	)
  AND PatientPopulationPercentageBelowPoverty > 15
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### The `ORDER BY` Clauses 

You can order the the rows by column(s) using the `ORDER BY` clause. This clause is put after the `WHERE` clause. You can specify
multiple columns separated by comma. You can also specify ascending order using the `ASC` keyword after the column name 
and descending order by using the `DESC` keyword. The default sorting order is ascending. A shortcut for descending is putting `-` before the column name. Finally
you can sort the columns by its numerical position.

#### Sort by columns

**Query:** Select the `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` columns from 
the `PatientCorePopulatedTable` table and sort by `PatientPopulationPercentageBelowPoverty`.

```sql
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientPopulationPercentageBelowPoverty;
```

In [43]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientPopulationPercentageBelowPoverty;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

**Query:** Select the `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` columns from 
the `PatientCorePopulatedTable` table and sort by `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty`.

```sql
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, PatientPopulationPercentageBelowPoverty;
```

In [44]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, PatientPopulationPercentageBelowPoverty;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Ascending versus Descending Sort Order

**Query:** Select the `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` columns from 
the `PatientCorePopulatedTable` table and sort by `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` by descending order
using the keyword `DESC`.

```sql
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, PatientPopulationPercentageBelowPoverty DESC;
```

In [45]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, PatientPopulationPercentageBelowPoverty DESC;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

**Query:** Select the `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` columns from 
the `PatientCorePopulatedTable` table and sort by `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` by descending order
using the `-`.

```sql
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, -PatientPopulationPercentageBelowPoverty;
```

In [46]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, -PatientPopulationPercentageBelowPoverty;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

#### Sorting using numerical position

When sorting by numerical position, you cannot use `-`. You must use the keyword `DESC`. Column names make your code more explicit, which you should prefer. 

**Query:** Select the `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` columns from 
the `PatientCorePopulatedTable` table and sort by `PatientMaritalStatus` and `PatientPopulationPercentageBelowPoverty` by descending order
using the keyword `DESC`, but using the numerical position of `PatientPopulationPercentageBelowPoverty`. 

```sql
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, 2 DESC;
```

In [47]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
  PatientMaritalStatus, 
  PatientPopulationPercentageBelowPoverty
FROM
  PatientCorePopulatedTable
ORDER BY PatientMaritalStatus, 2 DESC;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 3. FILTERING

### Logical Operators

| Operator | What it does?                                        |
|----------|------------------------------------------------------|
| `AND`    | True if both conditions are true  | 
| `OR`     | True if one of two conditions is true |
| `NOT`    | Negate a specified condition |
| `IN` | Allows for multiple OR conditions |
| `NOT IN`    | Negate multiple AND conditions  |
| `EXISTS`    | True if a record exists |
| `LIKE`    | True if there is a string match using % |

### Relational Operators

Assume `a=1` and `b=1`

| Relational Operators | What it does?             |
|----|---------------------------------------------|
| = | True if a has the same value as b           |
| <>, != | True if a does not have the same value as b |
| >  | True if a is greater than b                 |
| <  | True if a is less than b                    |
| >= | True if a is greater than or equal to b     |
| <= | True if a is less than or equal to b        |

### Conditional Evaluation 

In [48]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE PatientGender = 'Male' AND PatientDateOfBirth < '1950-01-01'
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Using Parenthesis

In [49]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE (PatientGender = 'Male' OR PatientRace = 'White') AND PatientDateOfBirth < '1950-01-01'
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Using the `NOT` Operator

In [50]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE NOT (PatientGender = 'Male' OR PatientRace = 'White') AND PatientDateOfBirth < '1950-01-01'
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Inequality condition

In [51]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE (PatientGender = 'Male' AND PatientRace <> 'White') AND PatientDateOfBirth < '1950-01-01'
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Range using `BETWEEN` condition

In [52]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE PatientDateOfBirth BETWEEN '1920-01-01' AND '1965-01-01'
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### String Condition

In [53]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE PatientID BETWEEN '2A' AND '53'
ORDER BY PatientID
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Membership Condition

In [54]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE PatientRace = 'White' OR PatientRace = 'Asian'
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### `IN` condition

In [55]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE PatientRace IN ('White', 'Asian')
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### `NOT IN` condition

In [56]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE PatientRace NOT IN ('White', 'Asian')
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Using subqueries

In [57]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM PatientCorePopulatedTable
WHERE PatientID IN (SELECT PatientID FROM PatientCorePopulatedTable WHERE PatientDateOfBirth > '1980-01-01')
ORDER BY PatientDateOfBirth
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Using Wildcards

In [58]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM AdmissionsDiagnosesCorePopulatedTable
WHERE PrimaryDiagnosisCode LIKE 'M%'
ORDER BY PrimaryDiagnosisCode
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Checking for NULL

In [59]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/cars.db')

sql_statement = """
SELECT *
FROM Cars
WHERE color_id IS NULL
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 4. SETS

SQL supports four types of operations `UNION`, `UNION ALL`, `INTERSECT`, and `EXCEPT`. The difference between `UNION` and `UNION ALL` is that the latter includes duplicates. 
Given set A = {L, M, N, O, P} and set B = {P, Q, R, S, T}, the four operations will return
1. A UNION B  = {L, M, N, O, P, Q, R, S, T}
2. A UNION ALL = {L, M, N, O, P, P, Q, R, S, T} -- Note the two Ps
3. A INTERSECT B = {P}
4. A EXCEPT B = {L, M N, O}

When doing set operations, you should use the same column names so you can order the results. 

### The `UNION ALL`  and `UNION` Operator

In [60]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/students_teachers.db')

sql_statement = """
SELECT 
    'Teacher' typ,
    t.first_name
FROM Teachers t
WHERE t.first_name LIKE 'Jo%'
UNION ALL
SELECT 
    'Student' typ,
    s.first_name
FROM Students s
WHERE s.first_name LIKE 'Jo%'
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [61]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/students_teachers.db')

sql_statement = """
SELECT 
    t.first_name
FROM Teachers t
WHERE t.first_name LIKE 'Jo%'
UNION ALL
SELECT 
    s.first_name
FROM Students s
WHERE s.first_name LIKE 'Jo%'
ORDER BY first_name
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [62]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/students_teachers.db')

sql_statement = """
SELECT 
    t.first_name
FROM Teachers t
WHERE t.first_name LIKE 'Jo%'
UNION
SELECT 
    s.first_name
FROM Students s
WHERE s.first_name LIKE 'Jo%'
ORDER BY first_name
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### The `INTERSECT` Operator

In [63]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/students_teachers.db')

sql_statement = """
SELECT 
    t.first_name
FROM Teachers t
WHERE t.first_name LIKE 'Jo%'
INTERSECT 
SELECT 
    s.first_name
FROM Students s
WHERE s.first_name LIKE 'Jo%'
ORDER BY first_name
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### The `EXCEPT` Operator

In [64]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/students_teachers.db')

sql_statement = """
SELECT 
    t.first_name
FROM Teachers t
WHERE t.first_name LIKE 'Jo%'
EXCEPT
SELECT 
    s.first_name
FROM Students s
WHERE s.first_name LIKE 'Jo%'
ORDER BY first_name
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 5. GROUPING AND AGGREGATES

The `GROUP BY` allows you to group values together and then apply one of the following five functions
1. `MAX()`
2. `MIN()`
3. `AVG()`
4. `SUM()`
5. `COUNT()`

The `HAVING` keyword, which follows the `GROUP BY` keyword allows you to filter the aggregated results. 

### A Simple Grouping Examples

In [65]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT PatientID, Count(LabName) LabCount
FROM LabsCorePopulatedTable 
GROUP BY PatientID
ORDER BY -LabCount
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [66]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT PatientID, Count(LabName) LabCount
FROM LabsCorePopulatedTable 
GROUP BY PatientID
HAVING LabCount > 2000
ORDER BY -LabCount
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [67]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT PatientID, Count(LabName) LabCount, Max(LabValue),  Min(LabValue),  SUM(LabValue), ROUND(AVG(LabValue),2) AVERAGE
FROM LabsCorePopulatedTable 
WHERE LabName = 'URINALYSIS: RED BLOOD CELLS'
GROUP BY PatientID
ORDER BY -AVERAGE
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Multicolumn Grouping

In [68]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT PatientID, LabName, Count(LabName) LabCount, Max(LabValue),  Min(LabValue),  SUM(LabValue), ROUND(AVG(LabValue),2) AVERAGE
FROM LabsCorePopulatedTable 
GROUP BY PatientID, LabName
ORDER BY -PatientID, -LabCount
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Date Difference

In [69]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT PatientID, ROUND(MAX(julianday(AdmissionEndDate)-julianday(AdmissionStartDate))) MAX_STAY
FROM AdmissionsCorePopulatedTable 
GROUP BY PatientID
HAVING MAX_STAY >= 20
ORDER BY -MAX_STAY
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 6. SUBQUERY

### Using value from a subquery

In [70]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT p.*, m.max_stay
FROM  PatientCorePopulatedTable  p
INNER JOIN 
(SELECT PatientID, ROUND(MAX(julianday(AdmissionEndDate)-julianday(AdmissionStartDate))) MAX_STAY
FROM AdmissionsCorePopulatedTable 
GROUP BY PatientID
HAVING MAX_STAY >= 15
) m
ON p.PatientID = m.PatientID
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### `IN` and `NOT IN` examples

In [71]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM  LabsCorePopulatedTable 
WHERE PatientID IN (
    SELECT PatientID 
    FROM PatientCorePopulatedTable 
    WHERE PatientLanguage IN ('Icelandic', 'Spanish')
)
LIMIT 100;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [72]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT *
FROM  LabsCorePopulatedTable 
WHERE PatientID IN (
    SELECT PatientID 
    FROM PatientCorePopulatedTable 
    WHERE PatientLanguage NOT IN ('Icelandic', 'Spanish')
)
LIMIT 100;
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 7. CONDITIONALS
https://www.mountsinai.org/health-library/tests/creatinine-blood-test

```
CASE
    WHEN C1 THEN E1
    WHEN C2 THEN E2
    ...
    WHEN CN THEN EN
    [ELSE ED]
END [COLUMN_NAME]
```

In [73]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
	CASE
		WHEN strftime('%m', AdmissionStartDate) = '01' THEN 'January'
		WHEN strftime('%m', AdmissionStartDate) = '02' THEN 'February'
		WHEN strftime('%m', AdmissionStartDate) = '03' THEN 'March'
		WHEN strftime('%m', AdmissionStartDate) = '04' THEN 'April'
		WHEN strftime('%m', AdmissionStartDate) = '05' THEN 'May'
		WHEN strftime('%m', AdmissionStartDate) = '06' THEN 'June'
		WHEN strftime('%m', AdmissionStartDate) = '07' THEN 'July'
		WHEN strftime('%m', AdmissionStartDate) = '08' THEN 'August'
		WHEN strftime('%m', AdmissionStartDate) = '09' THEN 'September'
		WHEN strftime('%m', AdmissionStartDate) = '10' THEN 'October'
		WHEN strftime('%m', AdmissionStartDate) = '11' THEN 'November'
		WHEN strftime('%m', AdmissionStartDate) = '12' THEN 'December'
	END AdmissionMonth,
	count(*) AddmissionCount
FROM 
	AdmissionsCorePopulatedTable
Group BY AdmissionMonth
ORDER BY -AddmissionCount
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [74]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
WITH AGE AS (
	SELECT 
	PATIENTID,
	ROUND((JULIANDAY('NOW') - JULIANDAY(PATIENTDATEOFBIRTH))/365.25) AGE
	FROM 
	PATIENTCOREPOPULATEDTABLE
)
SELECT 
	PATIENTID,
	AGE, 
	CASE 
		WHEN AGE < 18 THEN 'YOUTH'
		WHEN AGE BETWEEN 18 AND 35 THEN 'YOUNG ADULT'
		WHEN AGE BETWEEN 36 AND 55 THEN 'ADULT'
		WHEN AGE >= 56 THEN 'SENIOR'
	END AGERANGE
FROM 
	AGE
ORDER BY AGE
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [75]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
WITH AGE AS (
	SELECT 
	PATIENTID,
	ROUND((JULIANDAY('NOW') - JULIANDAY(PATIENTDATEOFBIRTH))/365.25) AGE
	FROM 
	PATIENTCOREPOPULATEDTABLE
)
SELECT 
	CASE 
		WHEN AGE < 18 THEN 'YOUTH'
		WHEN AGE BETWEEN 18 AND 35 THEN 'YOUNG ADULT'
		WHEN AGE BETWEEN 36 AND 55 THEN 'ADULT'
		WHEN AGE >= 56 THEN 'SENIOR'
	END AGE_RANGE,
	COUNT(*) AGE_RANGE_COUNT
FROM 
	AGE
GROUP BY AGE_RANGE
ORDER BY AGE
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [76]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    CAST (
        SUM(
            CASE
                WHEN PatientGender = 'Male'
                AND PatientMaritalStatus = 'Married' THEN 1
                ELSE 0
            END
        ) AS REAL
    ) / CAST (
        SUM(
            CASE
                WHEN PatientGender = 'Female'
                AND PatientMaritalStatus = 'Married' THEN 1
                ELSE 0
            END
        ) AS REAL
    ) MARRIED_MALE_FEMALE_RATIO
FROM
    PatientCorePopulatedTable
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [77]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    PatientID,
    CASE
        WHEN EXISTS(
            SELECT
                1
            FROM
                LabsCorePopulatedTable
            WHERE
                LabsCorePopulatedTable.PatientID = PatientCorePopulatedTable.PatientID
                AND LabsCorePopulatedTable.LabName = 'URINALYSIS: SPECIFIC GRAVITY'
        ) THEN 'Y'
        ELSE 'N'
    END 'URINALYSIS: SPECIFIC GRAVITY',
    CASE
        WHEN EXISTS(
            SELECT
                1
            FROM
                LabsCorePopulatedTable
            WHERE
                LabsCorePopulatedTable.PatientID = PatientCorePopulatedTable.PatientID
                AND LabsCorePopulatedTable.LabName = 'URINALYSIS: PH'
        ) THEN 'Y'
        ELSE 'N'
    END 'URINALYSIS: PH',
    CASE
        WHEN EXISTS(
            SELECT
                1
            FROM
                LabsCorePopulatedTable
            WHERE
                LabsCorePopulatedTable.PatientID = PatientCorePopulatedTable.PatientID
                AND LabsCorePopulatedTable.LabName = 'URINALYSIS: RED BLOOD CELLS'
        ) THEN 'Y'
        ELSE 'N'
    END 'URINALYSIS: RED BLOOD CELLS',
    CASE
        WHEN EXISTS(
            SELECT
                1
            FROM
                LabsCorePopulatedTable
            WHERE
                LabsCorePopulatedTable.PatientID = PatientCorePopulatedTable.PatientID
                AND LabsCorePopulatedTable.LabName = 'URINALYSIS: WHITE BLOOD CELLS'
        ) THEN 'Y'
        ELSE 'N'
    END 'URINALYSIS: WHITE BLOOD CELLS'
FROM
    PatientCorePopulatedTable
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [78]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    LabsCorePopulatedTable.PatientID,
    PatientCorePopulatedTable.PatientGender,
    LabName,
    LabValue,
    LabUnits,
    CASE
        WHEN PatientCorePopulatedTable.PatientGender = 'Male'
        AND LabValue BETWEEN 0.7
        AND 1.3 THEN 'Normal'
        WHEN PatientCorePopulatedTable.PatientGender = 'Female'
        AND LabValue BETWEEN 0.6
        AND 1.1 THEN 'Normal'
        ELSE 'Out of Range'
    END Interpretation
FROM
    LabsCorePopulatedTable
    JOIN PatientCorePopulatedTable ON PatientCorePopulatedTable.PatientID = LabsCorePopulatedTable.PatientID
WHERE
    LabName = 'METABOLIC: CREATININE'
ORDER BY
    - LabValue
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [79]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT
    case
        WHEN 0 + strftime('%m', AdmissionStartDate) BETWEEN 1
        AND 3 THEN 'Q1'
        WHEN 0 + strftime('%m', AdmissionStartDate) BETWEEN 4
        AND 6 THEN 'Q2'
        WHEN 0 + strftime('%m', AdmissionStartDate) BETWEEN 7
        AND 9 THEN 'Q3'
        WHEN 0 + strftime('%m', AdmissionStartDate) BETWEEN 10
        AND 12 THEN 'Q4'
    end as Quarter,
    CASE
        WHEN strftime('%m', AdmissionStartDate) = '01' THEN 'January'
        WHEN strftime('%m', AdmissionStartDate) = '02' THEN 'February'
        WHEN strftime('%m', AdmissionStartDate) = '03' THEN 'March'
        WHEN strftime('%m', AdmissionStartDate) = '04' THEN 'April'
        WHEN strftime('%m', AdmissionStartDate) = '05' THEN 'May'
        WHEN strftime('%m', AdmissionStartDate) = '06' THEN 'June'
        WHEN strftime('%m', AdmissionStartDate) = '07' THEN 'July'
        WHEN strftime('%m', AdmissionStartDate) = '08' THEN 'August'
        WHEN strftime('%m', AdmissionStartDate) = '09' THEN 'September'
        WHEN strftime('%m', AdmissionStartDate) = '10' THEN 'October'
        WHEN strftime('%m', AdmissionStartDate) = '11' THEN 'November'
        WHEN strftime('%m', AdmissionStartDate) = '12' THEN 'December'
    END AdmissionMonth,
    count(*) AddmissionCount
FROM
    AdmissionsCorePopulatedTable
GROUP BY
    Quarter,
    AdmissionMonth
ORDER BY
    strftime('%m', AdmissionStartDate)
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 8. ANALYTIC FUNCTIONS

Analytic functions allow you to group rows into windows, partitioning the data. Windows are defined using the `OVER` clause and optionally combined with the `PARTITION` subclause. 

Date Reference: https://www.techonthenet.com/sqlite/functions/julianday.php

### Data Windows

In [80]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
SELECT
    CASE
        WHEN 0 + strftime('%m', sale_date) BETWEEN 1
        AND 3 THEN 'Q1'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 4
        AND 6 THEN 'Q2'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 7
        AND 9 THEN 'Q3'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 10
        AND 12 THEN 'Q4'
    END Quarter,
    CASE
        WHEN strftime('%m', sale_date) = '01' THEN 'January'
        WHEN strftime('%m', sale_date) = '02' THEN 'February'
        WHEN strftime('%m', sale_date) = '03' THEN 'March'
        WHEN strftime('%m', sale_date) = '04' THEN 'April'
        WHEN strftime('%m', sale_date) = '05' THEN 'May'
        WHEN strftime('%m', sale_date) = '06' THEN 'June'
        WHEN strftime('%m', sale_date) = '07' THEN 'July'
        WHEN strftime('%m', sale_date) = '08' THEN 'August'
        WHEN strftime('%m', sale_date) = '09' THEN 'September'
        WHEN strftime('%m', sale_date) = '10' THEN 'October'
        WHEN strftime('%m', sale_date) = '11' THEN 'November'
        WHEN strftime('%m', sale_date) = '12' THEN 'December'
    END Month,
    sum(total) Monthly_Sales
FROM
    bakery_sales
GROUP BY
    Quarter,
    Month
ORDER BY 
	strftime('%m', sale_date)
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [81]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
WITH SalesTable AS (
SELECT
    CASE
        WHEN 0 + strftime('%m', sale_date) BETWEEN 1
        AND 3 THEN 'Q1'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 4
        AND 6 THEN 'Q2'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 7
        AND 9 THEN 'Q3'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 10
        AND 12 THEN 'Q4'
    END Quarter,
    CASE
        WHEN strftime('%m', sale_date) = '01' THEN 'January'
        WHEN strftime('%m', sale_date) = '02' THEN 'February'
        WHEN strftime('%m', sale_date) = '03' THEN 'March'
        WHEN strftime('%m', sale_date) = '04' THEN 'April'
        WHEN strftime('%m', sale_date) = '05' THEN 'May'
        WHEN strftime('%m', sale_date) = '06' THEN 'June'
        WHEN strftime('%m', sale_date) = '07' THEN 'July'
        WHEN strftime('%m', sale_date) = '08' THEN 'August'
        WHEN strftime('%m', sale_date) = '09' THEN 'September'
        WHEN strftime('%m', sale_date) = '10' THEN 'October'
        WHEN strftime('%m', sale_date) = '11' THEN 'November'
        WHEN strftime('%m', sale_date) = '12' THEN 'December'
    END Month, 
	Total
FROM
    bakery_sales
)
SELECT 
	Quarter,
	Month, 
	Sum(Total) MonthlySales,
	Max(sum(total)) over() max_overall_sales,
	Max(sum(total)) over(partition by quarter) max_quarter_sales
FROM SalesTable
GROUP BY Quarter, Month
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Localized Sorting

In [82]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
WITH SalesTable AS (
SELECT
    CASE
        WHEN 0 + strftime('%m', sale_date) BETWEEN 1
        AND 3 THEN 'Q1'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 4
        AND 6 THEN 'Q2'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 7
        AND 9 THEN 'Q3'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 10
        AND 12 THEN 'Q4'
    END Quarter,
    CASE
        WHEN strftime('%m', sale_date) = '01' THEN 'January'
        WHEN strftime('%m', sale_date) = '02' THEN 'February'
        WHEN strftime('%m', sale_date) = '03' THEN 'March'
        WHEN strftime('%m', sale_date) = '04' THEN 'April'
        WHEN strftime('%m', sale_date) = '05' THEN 'May'
        WHEN strftime('%m', sale_date) = '06' THEN 'June'
        WHEN strftime('%m', sale_date) = '07' THEN 'July'
        WHEN strftime('%m', sale_date) = '08' THEN 'August'
        WHEN strftime('%m', sale_date) = '09' THEN 'September'
        WHEN strftime('%m', sale_date) = '10' THEN 'October'
        WHEN strftime('%m', sale_date) = '11' THEN 'November'
        WHEN strftime('%m', sale_date) = '12' THEN 'December'
    END Month, 
	Total
FROM
    bakery_sales
)
SELECT 
	Quarter,
	Month, 
	Sum(Total) MonthlySales,
	rank() OVER (ORDER BY -sum(total)) SalesRank
FROM SalesTable
GROUP BY Quarter, Month
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [83]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
WITH SalesTable AS (
SELECT
    CASE
        WHEN 0 + strftime('%m', sale_date) BETWEEN 1
        AND 3 THEN 'Q1'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 4
        AND 6 THEN 'Q2'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 7
        AND 9 THEN 'Q3'
        WHEN 0 + strftime('%m', sale_date) BETWEEN 10
        AND 12 THEN 'Q4'
    END Quarter,
    CASE
        WHEN strftime('%m', sale_date) = '01' THEN 'January'
        WHEN strftime('%m', sale_date) = '02' THEN 'February'
        WHEN strftime('%m', sale_date) = '03' THEN 'March'
        WHEN strftime('%m', sale_date) = '04' THEN 'April'
        WHEN strftime('%m', sale_date) = '05' THEN 'May'
        WHEN strftime('%m', sale_date) = '06' THEN 'June'
        WHEN strftime('%m', sale_date) = '07' THEN 'July'
        WHEN strftime('%m', sale_date) = '08' THEN 'August'
        WHEN strftime('%m', sale_date) = '09' THEN 'September'
        WHEN strftime('%m', sale_date) = '10' THEN 'October'
        WHEN strftime('%m', sale_date) = '11' THEN 'November'
        WHEN strftime('%m', sale_date) = '12' THEN 'December'
    END Month, 
	Total
FROM
    bakery_sales
)
SELECT 
	Quarter,
	Month, 
	Sum(Total) MonthlySales,
	rank() OVER (PARTITION BY Quarter ORDER BY -sum(total)) SalesRank
FROM SalesTable
GROUP BY Quarter, Month
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Window Frames
https://www.sqlitetutorial.net/sqlite-window-functions/sqlite-window-frame/

In [84]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
WITH SalesTable AS (
SELECT
	cast(strftime('%Y', sale_date) AS INT) sale_year,
	cast(strftime('%W', sale_date) AS INT) sale_week,
	Total
FROM
    bakery_sales
ORDER BY sale_date
)
SELECT 
	sale_year,
	sale_week,
	sum(total) week_total,
	sum(sum(total)) OVER (ORDER BY sale_year, sale_week ROWS UNBOUNDED PRECEDING) rolling_sum
FROM SalesTable
GROUP BY sale_year, sale_week
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [85]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
SELECT 
	sale_date,
	sum(total) total,
	max(sum(total)) over (order by cast(strftime('%j', sale_date) AS INT) range between 3 preceding and 3 following) seven_day_max
FROM bakery_sales
GROUP BY sale_date
order by sale_date
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Lag and Lead

In [86]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
WITH SalesTable AS (
SELECT
	cast(strftime('%Y', sale_date) AS INT) sale_year,
	cast(strftime('%W', sale_date) AS INT) sale_week,
	Total
FROM
    bakery_sales
ORDER BY sale_date
)
SELECT 
	sale_year,
	sale_week,
	sum(total) week_total,
	lag(sum(total), 1) over (order by sale_week) prev_week_total,
	lead(sum(total), 1) over (order by sale_week) next_week_total
FROM SalesTable
GROUP BY sale_year, sale_week
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

In [87]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/bakery_sales.db')

sql_statement = """
WITH SalesTable AS (
    SELECT
        cast(strftime('%Y', sale_date) AS INT) sale_year,
        cast(strftime('%W', sale_date) AS INT) sale_week,
        Total
    FROM
        bakery_sales
    ORDER BY
        sale_date
)
SELECT
    sale_year,
    sale_week,
    sum(total) week_total,
    round(
        CAST(
            (
                sum(total) - lag(sum(total), 1) over (
                    order by
                        sale_week
                )
            ) AS REAL
        ) / CAST(
            lag(sum(total), 1) over (
                order by
                    sale_week
            ) AS REAL
        ) * 100,
        1
    ) CHANGE
FROM
    SalesTable
GROUP BY
    sale_year,
    sale_week
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

### Ranking

- `rank`: returns the same ranking in case of a tie, with gaps in the rankings
- `row_number`: returns a unique number for each row, with rankings arbitrarily assigned in case of a tie
- `dense_rank`: returns the same ranking in the case of a tie, with no gaps in the rankings

Ref: https://blog.jooq.org/the-difference-between-row_number-rank-and-dense_rank/

In [88]:
import sqlite3
import pandas as pd

conn = sqlite3.connect('./data/100_patients.db')

sql_statement = """
SELECT 
	PatientGender,
	PatientMaritalStatus, 
	count(*) StatusCount, 
	rank() OVER (PARTITION BY PatientGender ORDER BY COUNT(*) DESC) StatusRank,
	row_number() OVER (PARTITION BY PatientGender ORDER BY COUNT(*) DESC) StatusRowNumber,
	dense_rank() OVER (PARTITION BY PatientGender ORDER BY COUNT(*) DESC) StatusDenseRank
FROM 
PatientCorePopulatedTable
GROUP BY PatientGender, PatientMaritalStatus
"""
df = pd.read_sql_query(sql_statement, conn)
df.style.set_table_attributes('style="font-size: 12px"')

## 9.NORMALIZATION

What is database normalization?
- Ref: https://www.complexsql.com/database-normalization/
- Ref: http://www.databasedev.co.uk/1norm_form.html
- The purpose of database normalization is to:
- eliminate redundant data
- reduce complexity of data, making it easier to manage the data and make change
- ensure logical data dependencies
- How is database normalization achieved?
  - By fulfilling five normal forms. Each normal form represents an increasingly stringent set of rules. Usually fulfilling the first three normal forms is sufficient.
  - Ref: https://www.1keydata.com/database-normalization/first-normal-form-1nf.php
- First Normal Form  (1NF): 
  1. if there are no repeating groups.
  2. all values are atomic, meaning they are the smallest meaningful value
- Second Normal Form  (2NF): 
  1. the table is in first normal form
  2. each non-key field is functionally dependent on the entire primary key
- Third Normal Form (3NF):
  1. the table is in second normal form
  2. there are no transitive dependencies
- Ref: https://arctype.com/blog/2nf-3nf-normalization-example/
- Summary
  1. All values must be atomic
  2. No redundancy
  3. No implicit relationship/dependency
  4. No transitive relationship/dependency

## 10. PYTHON AND SQLITE3

### Basic example

In [89]:
import pandas as pd
import sqlite3
conn = sqlite3.connect("./data/join_example_database.db")
sql_statement = "select Quantities.product, Quantities.quantity FROM Quantities"
df = pd.read_sql_query(sql_statement, conn)
display(df)

PRODUCT  QUANTITY
0  Potatoes        45
1  Avacados        63
2     Kiwis        19
3    Onions        20
4    Melons        66
5  Broccoli        27
6    Squash        92

### Utility functions
- Two utility functions are provided that you will use often

In [90]:
import sqlite3
from sqlite3 import Error


def create_connection(db_file):
    conn = None
    try:
        conn = sqlite3.connect(db_file)
    except Error as e:
        print(e)

    return conn


def create_table(conn, create_table_sql):
    try:
        c = conn.cursor()
        c.execute(create_table_sql)
    except Error as e:
        print(e)

### Example SQL query using Python

```python
db_file = './data/student_test_in_class.db'
conn = create_connection(db_file)
cur = conn.cursor()
cur.execute("SELECT first_name, last_name FROM Students")

rows = cur.fetchall()

for row in rows:
    print(row)
```

### Steps to creating a database using Python

1. Write a create table sql statement(s)
2. Write insert function(s)
3. Read files or data and use the insert function(s) to insert data into table

#### Create a database and populate from a file

In [91]:
import os
db_file = './data/student_test_in_class.db'
if os.path.exists(db_file):
    os.remove(db_file)

create_table_sql = """
CREATE TABLE students (
    last_name TEXT,
    first_name TEXT,
    username TEXT,
    exam1 REAL,
    exam2 REAL,
    exam3 REAL
);
"""

conn = create_connection(db_file)


def insert_student(conn, values):
    sql = ''' INSERT INTO students(last_name,first_name,username,exam1,exam2,exam3)
              VALUES(?,?,?,?,?,?) '''
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid

with conn:
    # create
    create_table(conn, create_table_sql)

    # insert
    for student in open('./data/students.tsv', 'r'):
        values = student.strip().split('\t')
        print(values)
        rid = insert_student(conn, values) ## What is rid?

['Larson', 'Melissa', 'larsonmeli', '24', '89', '31']
['Novak', 'Melissa', 'novakmeli', '77', '3', '38']
['Sawyer', 'Wendy', 'sawyerwend', '81', '59', '30']
['Schultz', 'Marcus', 'schultzmarc', '59', '29', '67']
['Vega', 'Nicholas', 'veganich', '64', '12', '95']
['Adams', 'Brenda', 'adamsbren', '80', '49', '60']
['Thompson', 'Charlene', 'thompsonchar', '37', '56', '26']
['Booth', 'Bradley', 'boothbrad', '85', '8', '77']
['Gallegos', 'Eugene', 'gallegoseuge', '34', '9', '76']
['Munoz', 'Mary', 'munozmary', '77', '41', '55']
['Carey', 'Kimberly', 'careykimb', '29', '94', '23']
['Paul', 'Philip', 'paulphil', '79', '86', '60']
['Reed', 'Madeline', 'reedmade', '16', '39', '46']
['Parsons', 'Cassie', 'parsonscass', '61', '62', '65']
['Mcclain', 'Glenn', 'mcclainglen', '85', '98', '52']
['Oliver', 'Janice', 'oliverjani', '72', '47', '34']
['Lozano', 'Catherine', 'lozanocath', '71', '19', '94']
['Klein', 'John', 'kleinjohn', '3', '43', '88']
['Brooks', 'Marcus', 'brooksmarc', '6', '81', '70']


#### Fetch data

In [92]:
sql_statement = "SELECT * FROM Students"
df = pd.read_sql_query(sql_statement, conn)
display(df)

last_name first_name       username  exam1  exam2  exam3
0      Larson    Melissa     larsonmeli   24.0   89.0   31.0
1       Novak    Melissa      novakmeli   77.0    3.0   38.0
2      Sawyer      Wendy     sawyerwend   81.0   59.0   30.0
3     Schultz     Marcus    schultzmarc   59.0   29.0   67.0
4        Vega   Nicholas       veganich   64.0   12.0   95.0
..        ...        ...            ...    ...    ...    ...
95     Duncan     Andrew     duncanandr   59.0   87.0   34.0
96       Bush  Alexander       bushalex   82.0   54.0   25.0
97    Summers    Michael    summersmich   18.0   95.0   63.0
98     Bowers     Sandra     bowerssand   52.0    8.0   50.0
99  Fernandez   Jonathan  fernandezjona   74.0   80.0   22.0

[100 rows x 6 columns]

### Another example

In [93]:
# 1 -- create table sql statements
# 2 -- create insert functions
# 3 -- read files or data and use the insert function


db = './data/depts_students.db'
if os.path.exists(db):
    os.remove(db)

create_table_departments_sql = """ CREATE TABLE [Departments] (
    [DepartmentId] INTEGER  NOT NULL PRIMARY KEY,
    [DepartmentName] TEXT 
); """

create_table_students_sql = """CREATE TABLE [Students] (
    [StudentId] INTEGER  PRIMARY KEY NOT NULL,
    [StudentName] TEXT NOT NULL,
    [DepartmentId] INTEGER,
    [DateOfBirth] DATE,
    FOREIGN KEY(DepartmentId) REFERENCES Departments(DepartmentId)
);"""


depts = ('IT', 'Physics', 'Arts', 'Math')

students = (
    ('Michael', 1, '1998-10-12'),
    ('John', 1, '1998-10-12'),
    ('Jack', 1, '1998-10-12'),
    ('Sara', 2, '1998-10-12'),
    ('Sally', 2, '1998-10-12'),
    ('Jena', None, '1998-10-12'),
    ('Nancy', 2, '1998-10-12'),
    ('Adam', 3, '1998-10-12'),
    ('Stevens', 3, '1998-10-12'),
    ('George', None, '1998-10-12')
)

def insert_depts(conn, values):
    sql = ''' INSERT INTO Departments(DepartmentName)
              VALUES(?) '''
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid


def insert_student(conn, values):
    sql = ''' INSERT INTO Students(StudentName, DepartmentId, DateOfBirth)
              VALUES(?,?,?) '''
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid

conn = create_connection(db)

with conn:

    create_table(conn, create_table_departments_sql)
    create_table(conn, create_table_students_sql)
    for values in depts:
        insert_depts(conn, (values, ))
        
    for values in students:
        insert_student(conn, values)

# MAKING THE TABLE
sql_statement = "SELECT * FROM Students"
df = pd.read_sql_query(sql_statement, conn)
display(df)

# FETCH ALL
cur = conn.cursor()
cur.execute('SELECT * FROM Departments')
for row in cur.fetchall():  
    print(row)

# FETCH ONE
cur.execute('SELECT * FROM Departments')
print(cur.fetchone())
print(cur.fetchone())
print(cur.fetchone())
print(cur.fetchone())
print(cur.fetchone())

StudentId StudentName  DepartmentId DateOfBirth
0          1     Michael           1.0  1998-10-12
1          2        John           1.0  1998-10-12
2          3        Jack           1.0  1998-10-12
3          4        Sara           2.0  1998-10-12
4          5       Sally           2.0  1998-10-12
5          6        Jena           NaN  1998-10-12
6          7       Nancy           2.0  1998-10-12
7          8        Adam           3.0  1998-10-12
8          9     Stevens           3.0  1998-10-12
9         10      George           NaN  1998-10-12

(1, 'IT')
(2, 'Physics')
(3, 'Arts')
(4, 'Math')
(1, 'IT')
(2, 'Physics')
(3, 'Arts')
(4, 'Math')
None


### Creating a foreign key dictionary 

- Creating a foreign key dictionary lookup speeds things up because you are avoiding multiple call to the database

In [94]:
conn = create_connection(db)
cur = conn.cursor()
cur.execute('SELECT * FROM Departments')
dept_fk_lookup = {}
for row in cur.fetchall():
    key, text = row
    dept_fk_lookup[text] = key
print(dept_fk_lookup)

{'IT': 1, 'Physics': 2, 'Arts': 3, 'Math': 4}


## 11. EXAMPLE - SOCCER DATABASE

A sample input.

In [1]:
import pandas as pd
import sqlite3
from sqlite3 import Error
from collections import Counter

In [2]:
df = pd.read_csv('./data/all_players.csv')
df['Club'].isna().sum()

5493

In [3]:
conn = sqlite3.connect('all_players.db')
cur = conn.cursor()
df.to_sql('players', conn, if_exists='replace', index=False) # - writes the all_players.df to SQLIte DB
conn.commit()
conn.close()

In [4]:
def create_connection(db_file, delete_db=False):
    import os
    if delete_db and os.path.exists(db_file):
        os.remove(db_file)

    conn = None
    try:
        conn = sqlite3.connect(db_file)
        conn.execute("PRAGMA foreign_keys = 1")
    except Error as e:
        print(e)

    return conn


def create_table(conn, create_table_sql):
    try:
        c = conn.cursor()
        c.execute(create_table_sql)
    except Error as e:
        print(e)
        
def execute_sql_statement(sql_statement, conn):
    cur = conn.cursor()
    cur.execute(sql_statement)
    rows = cur.fetchall()

    return rows

In [5]:
display(df)

Player Club  POS  GP  GS  MINS  Year Season
0           Roy Lassiter  TB     F  30  30  2580  1996    reg
1         Raul Diaz Arce  DC     F  28  28  2351  1996    reg
2        Eduardo Hurtado  LA     F  26  26  2323  1996    reg
3                  Preki  KC     M  32  32  2880  1996    reg
4          Brian McBride  CLB    F  28  28  2307  1996    reg
...                  ...  ...  ...  ..  ..   ...   ...    ...
15762  Alejandro Pozuelo  NaN    M   1   1   120  2020   post
15763        Franco Jara  NaN    F   2   2   210  2020   post
15764          Andy Polo  NaN    M   1   1   105  2020   post
15765    Cristian Roldan  NaN    M   4   4   360  2020   post
15766       Joevin Jones  NaN  D-M   4   4   260  2020   post

[15767 rows x 8 columns]

### Tables

- Club
- Position
- Year
- Season
- Player
- PlayerStats

In [6]:
# Connecting the database
conn = sqlite3.connect('./data/all_players.db')

In [7]:
sql_statement = "SELECT DISTINCT CLUB FROM players"
rows = execute_sql_statement(sql_statement, conn)
rows = filter(lambda row: row[0], rows)
clubs = list(map(lambda row: row[0].strip(), rows))
clubs = list(set(clubs))

In [8]:
counter = Counter(clubs)
print(counter)

Counter({'SLV': 1, 'JAM': 1, 'DAL': 1, 'POR': 1, 'MTL': 1, 'LAFC': 1, 'COL': 1, 'GHA': 1, 'LFC': 1, 'TB': 1, 'MET': 1, 'CAN': 1, 'PHI': 1, 'CIN': 1, 'ECU': 1, 'CHV': 1, 'SKC': 1, 'SEA': 1, 'PAN': 1, 'HON': 1, 'MIA': 1, 'VAN': 1, 'CIV': 1, 'MTQ': 1, 'ORL': 1, 'CHI': 1, 'MCF': 1, 'LA': 1, 'SJ': 1, 'MIN': 1, 'NYC': 1, 'RSL': 1, 'NE': 1, 'HAI': 1, 'RBNY': 1, 'ROC': 1, 'TOR': 1, 'DC': 1, 'NSH': 1, 'USA': 1, 'HOU': 1, 'ATL': 1, 'NYR': 1, 'NY': 1, 'KC': 1, 'CLB': 1})


In [10]:
conn_norm = create_connection('players_norm.db', True)
create_table_sql = """CREATE TABLE IF NOT EXISTS[Clubs] (
    [Club] TEXT NOT NULL PRIMARY KEY
);
"""
create_table(conn_norm, create_table_sql) # doesn't require commit

In [11]:
def insert_club(conn, values):
    sql = """INSERT INTO Clubs(Club)
                VALUES(?)"""
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid


with conn_norm:
    for club in clubs:
        insert_club(conn_norm, (club,))

In [12]:
sql_statement = "SELECT DISTINCT CLUB FROM Clubs"
rows = execute_sql_statement(sql_statement, conn_norm)
print(rows)

[('SLV',), ('JAM',), ('DAL',), ('POR',), ('MTL',), ('LAFC',), ('COL',), ('GHA',), ('LFC',), ('TB',), ('MET',), ('CAN',), ('PHI',), ('CIN',), ('ECU',), ('CHV',), ('SKC',), ('SEA',), ('PAN',), ('HON',), ('MIA',), ('VAN',), ('CIV',), ('MTQ',), ('ORL',), ('CHI',), ('MCF',), ('LA',), ('SJ',), ('MIN',), ('NYC',), ('RSL',), ('NE',), ('HAI',), ('RBNY',), ('ROC',), ('TOR',), ('DC',), ('NSH',), ('USA',), ('HOU',), ('ATL',), ('NYR',), ('NY',), ('KC',), ('CLB',)]


In [13]:
sql_statement = "SELECT DISTINCT POS FROM players"
rows = execute_sql_statement(sql_statement, conn)
rows = filter(lambda row: row[0], rows)
positions = list(map(lambda row: row[0].strip(), rows))
positions = list(set(positions))
print(positions)

['M', 'M-D', 'F', 'F-M', 'D', 'D-M', 'M-F']


In [14]:
create_table_sql = """CREATE TABLE IF NOT EXISTS[Positions] (
    [Position] TEXT NOT NULL PRIMARY KEY
);
"""
create_table(conn_norm, create_table_sql) # doesn't require commit

In [15]:
def insert_position(conn, values):
    sql = """INSERT INTO Positions(Position)
                VALUES(?)"""
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid

with conn_norm:
    for position in positions:
        insert_position(conn_norm, (position,))

In [16]:
sql_statement = "SELECT DISTINCT Year FROM players"
rows = execute_sql_statement(sql_statement, conn)
rows = filter(lambda row: row[0], rows)
years = list(map(lambda row: int(row[0]), rows))
years = list(set(years))

In [17]:
create_table_sql = """CREATE TABLE IF NOT EXISTS[Years] (
    [Year] INTEGER NOT NULL PRIMARY KEY
);
"""
create_table(conn_norm, create_table_sql) # doesn't require commit

In [18]:
def insert_year(conn, values):
    sql = """INSERT INTO Years(Year)
                VALUES(?)"""
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid

with conn_norm:
    for year in years:
        insert_year(conn_norm, (year,))

In [19]:
sql_statement = "SELECT DISTINCT season FROM players"
rows = execute_sql_statement(sql_statement, conn)
rows = filter(lambda row: row[0], rows)
seasons = list(map(lambda row: row[0].strip(), rows))
seasons = list(set(seasons))

In [20]:
create_table_sql = """CREATE TABLE IF NOT EXISTS[Seasons] (
    [Season] TEXT NOT NULL PRIMARY KEY
);
"""
create_table(conn_norm, create_table_sql) # doesn't require commit

In [21]:
def insert_season(conn, values):
    sql = """INSERT INTO Seasons(season)
                VALUES(?)"""
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid

with conn_norm:
    for season in seasons:
        insert_season(conn_norm, (season,))

In [22]:
sql_statement = "SELECT DISTINCT player FROM players"
rows = execute_sql_statement(sql_statement, conn)
players = []
for row in rows:
    row = row[0].strip()
    name = row.split(' ', 1)
    if len(name) == 2:
        first, last = name
        first = first.strip()
        last = last.strip()
        players.append((first, last))
    elif len(name) == 1:
        first = name[0]
        players.append((first, None))

In [23]:
create_table_sql = """CREATE TABLE IF NOT EXISTS[Players] (
    [PlayerID] INTEGER NOT NULL PRIMARY KEY,
    [FirstName] TEXT NOT NULL,
    [LastName] TEXT
);
"""
create_table(conn_norm, create_table_sql) # doesn't require commit

In [24]:
def insert_player(conn, values):
    sql = """INSERT INTO Players(FirstName, LastName)
                VALUES(?, ?)"""
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid

with conn_norm:
    for player in players:
        insert_player(conn_norm, player)

In [26]:
create_table_sql = """CREATE TABLE IF NOT EXISTS[PlayerStats] (
    [StatID] INTEGER NOT NULL PRIMARY KEY,
    [PlayerID] INTEGER NOT NULL,
    [Club] TEXT,
    [Position] TEXT NOT NULL,
    [GP] INTEGER NOT NULL,
    [GS] INTEGER NOT NULL,
    [MIN] INTEGER NOT NULL,
    [Year] INTEGER NOT NULL,
    [Season] TEXT NOT NULL,
    FOREIGN KEY(PlayerID) REFERENCES Players(PlayerID),
    FOREIGN KEY(Club) REFERENCES Clubs(Club),
    FOREIGN KEY(Year) REFERENCES Years(Year),
    FOREIGN KEY(Season) REFERENCES Seasons(Season)     
);
"""

create_table(conn_norm, create_table_sql) # doesn't require commit

In [27]:
sql_statement = "SELECT DISTINCT * FROM players"
rows = execute_sql_statement(sql_statement, conn)
rows[:10]

[('Roy Lassiter', 'TB ', 'F', 30, 30, 2580, 1996, 'reg'),
 ('Raul Diaz Arce', 'DC ', 'F', 28, 28, 2351, 1996, 'reg'),
 ('Eduardo Hurtado', 'LA ', 'F', 26, 26, 2323, 1996, 'reg'),
 ('Preki', 'KC ', 'M', 32, 32, 2880, 1996, 'reg'),
 ('Brian McBride', 'CLB', 'F', 28, 28, 2307, 1996, 'reg'),
 ('Steve Rammel', 'DC ', 'F', 26, 20, 1649, 1996, 'reg'),
 ('Vitalis Takawira', 'KC ', 'F', 28, 25, 2233, 1996, 'reg'),
 ('Paul Bravo', 'SJ ', 'M', 31, 31, 2654, 1996, 'reg'),
 ('Jason Kreis', 'DAL', 'M', 31, 29, 2564, 1996, 'reg'),
 ('Giovanni Savarese', 'MET', 'F', 26, 15, 1576, 1996, 'reg')]

In [28]:
sql_statement = "SELECT * FROM players"
rows = execute_sql_statement(sql_statement, conn_norm)
player_lookup_dict = {}
for row in rows:
    pid, first, last = row
    if last:
        name = f'{first} {last}'
        player_lookup_dict[name] = pid
    else:
        player_lookup_dict[first] = pid

In [29]:
sql_statement = "SELECT DISTINCT * FROM players"
rows = execute_sql_statement(sql_statement, conn)

def insert_playerstats(conn, values):
    sql = """INSERT INTO PlayerStats(PlayerID, Club, position, gp, gs, min, year, season)
                VALUES(?, ?, ?, ?, ?, ?, ?,?)"""
    cur = conn.cursor()
    cur.execute(sql, values)
    return cur.lastrowid

with conn_norm:
    for row in rows:
        row = list(row)
        pid = player_lookup_dict[row[0].strip()]            
        row[0] = pid
        if not row[1]:
            continue
        row[1] = row[1].strip()
        insert_playerstats(conn_norm, row)